In [0]:
%pip install --upgrade wordcloud matplotlib

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
%restart_python

In [0]:
from pyspark.sql import SparkSession
from pyspark.ml.feature import Tokenizer
from pyspark.sql.functions import col, count, avg, max, min, size, concat_ws, collect_list, udf
import pandas as pd
from wordcloud import WordCloud
import matplotlib.pyplot as plt
import re
from pyspark.sql.types import StringType
from pyspark.ml.feature import StringIndexer, CountVectorizer, MinMaxScaler, IDF
from pyspark.ml.classification import NaiveBayes
from pyspark.ml.feature import Tokenizer,CountVectorizer,StandardScaler,PCA,StringIndexer
from pyspark.ml import Pipeline
from pyspark.ml.classification import LogisticRegression 
from pyspark.ml.evaluation import MulticlassClassificationEvaluator


Scarico nuovamente la tabella df_filtered_full per poterla utilizzare in questo notebook e poter costruire il modello di classificazione.

In [0]:
# Percorso del file Delta Lake
input_path = "/dbfs/tmp/delta_table"

# Leggi la tabella Delta Lake in un DataFrame
df_filtered_full = spark.read.format("delta").load(input_path)

# Mostra il contenuto del DataFrame
display(df_filtered_full)




title summary documents categoria doc_tokens sum_tokens filtered_doc_tokens filtered_sum_tokens doc_token_count sum_token_count baymina ankara power station baymina ankara power station (turkish: hamitabat doğal gaz kombine çevrim santrali) is a gas-fired power station in ankara province central turkey. baymina ankara power station (turkish: hamitabat doğal gaz kombine çevrim santrali) is a gas-fired power station in ankara province central turkey. == references == energy List(baymina, ankara, power, station, (turkish:, hamitabat, doğal, gaz, kombine, çevrim, santrali), is, a, gas-fired, power, station, in, ankara, province, central, turkey., ==, references, ==) List(baymina, ankara, power, station, (turkish:, hamitabat, doğal, gaz, kombine, çevrim, santrali), is, a, gas-fired, power, station, in, ankara, province, central, turkey.) List(baymina, ankara, power, station, (turkish:, hamitabat, doğal, gaz, kombine, çevrim, santrali), gas-fired, power, station, ankara, province, central, turkey., ==, references, ==) List(baymina, ankara, power, station, (turkish:, hamitabat, doğal, gaz, kombine, çevrim, santrali), gas-fired, power, station, ankara, province, central, turkey.) 21 18 xiju power plant the xiju power plant (chinese: 西莒發電廠; pinyin: xījǔ fādiànchǎng) is a diesel-fuel power plant in xiju island, juguang township, lienchiang county, taiwan. the xiju power plant (chinese: 西莒發電廠; pinyin: xījǔ fādiànchǎng) is a diesel-fuel power plant in xiju island, juguang township, lienchiang county, taiwan. history the power plant was commissioned in 1979. due to the changes in electricity needs, xiju power plant was connected by submarine power cable to dongju power plant in dongju island since 2000. see also list of power stations in taiwan electricity sector in taiwan == references == energy List(the, xiju, power, plant, (chinese:, 西莒發電廠;, pinyin:, xījǔ, fādiànchǎng), is, a, diesel-fuel, power, plant, in, xiju, island,, juguang, township,, lienchiang, county,, taiwan., history, the, power, plant, was, commissioned, in, 1979., due, to, the, changes, in, electricity, needs,, xiju, power, plant, was, connected, by, submarine, power, cable, to, dongju, power, plant, in, dongju, island, since, 2000., see, also, list, of, power, stations, in, taiwan, electricity, sector, in, taiwan, ==, references, ==) List(the, xiju, power, plant, (chinese:, 西莒發電廠;, pinyin:, xījǔ, fādiànchǎng), is, a, diesel-fuel, power, plant, in, xiju, island,, juguang, township,, lienchiang, county,, taiwan.) List(xiju, power, plant, (chinese:, 西莒發電廠;, pinyin:, xījǔ, fādiànchǎng), diesel-fuel, power, plant, xiju, island,, juguang, township,, lienchiang, county,, taiwan., history, power, plant, commissioned, 1979., due, changes, electricity, needs,, xiju, power, plant, connected, submarine, power, cable, dongju, power, plant, dongju, island, since, 2000., see, also, list, power, stations, taiwan, electricity, sector, taiwan, ==, references, ==) List(xiju, power, plant, (chinese:, 西莒發電廠;, pinyin:, xījǔ, fādiànchǎng), diesel-fuel, power, plant, xiju, island,, juguang, township,, lienchiang, county,, taiwan.) 53 18 bpscl power plant bpscl power plant is a coal-based thermal power plant located in bokaro district in the indian state of jharkhand. the power plant is owned by bokaro power supply company limited, a joint venture between steel authority of india and damodar valley corporation. it supplies power and process steam to bokaro steel plant and surplus power to grid.the plant's first unit was commissioned in 1982. bpscl power plant is a coal-based thermal power plant located in bokaro district in the indian state of jharkhand. the power plant is owned by bokaro power supply company limited, a joint venture between steel authority of india and damodar valley corporation. it supplies power and process steam to bokaro steel plant and surplus power to grid.the plant's first unit was commissioned in 1982. introduction bokaro power supply company limited (bpscl) came into be

#creazione del modello di classificazione

**Modello Logistic Regression per "documents"**

Avendo fatto in precedenza la tokenizzazione e la pulizia delle stopwords, utilizzo per addestrare il modello di regressione logistic il dataset con le sole colonne "filtered_doc_tokens" e "categoria".

In [0]:
df_doc = df_filtered_full.select("filtered_doc_tokens","categoria")

In [0]:
train, test = df_doc.randomSplit([0.8, 0.2], seed=42)

In [0]:
# Definire le fasi della pipeline, inclusa l'indicizzazione delle categorie
indexer = StringIndexer(inputCol="categoria", outputCol="categoria_indexed")
counter = CountVectorizer(inputCol="filtered_doc_tokens", outputCol="vector", vocabSize=5000)
scaler = StandardScaler(inputCol="vector", outputCol="scaled_features")
pca = PCA(k=200, inputCol="scaled_features", outputCol="pca_features")
scaler_pca = StandardScaler(inputCol="pca_features", outputCol="rescaled_features")

In [0]:
#modello logistic regression
lr = LogisticRegression(featuresCol="rescaled_features", labelCol="categoria_indexed")
# Creare la pipeline
pipe = Pipeline(stages=[indexer, counter, scaler, pca, scaler_pca, lr])

In [0]:
# Addestrare il modello
model = pipe.fit(train)

Valuto il modello con diverse metriche tramite la funzione "evaluation_model"

In [0]:
def evaluation_model(model, metrics, data):
    predictions = model.transform(data)
    evaluator = MulticlassClassificationEvaluator(labelCol="categoria_indexed", predictionCol="prediction", metricName=metrics)
    metric_value = evaluator.evaluate(predictions)
    return metric_value

In [0]:

# Valutazione del modello con diverse metriche per train set
accuracy_train = evaluation_model(model, "accuracy", train)
f1_train = evaluation_model(model, "f1", train)
precision_train = evaluation_model(model, "weightedPrecision", train)
recall_train = evaluation_model(model, "weightedRecall", train)

print(f"TRAIN: Accuracy: {accuracy_train}, F1: {f1_train}, Precision: {precision_train}, Recall: {recall_train}")


# valutazione del modello per test set
accuracy_test = evaluation_model(model, "accuracy", test)
f1_test = evaluation_model(model, "f1", test)
precision_test = evaluation_model(model, "weightedPrecision", test)
recall_test = evaluation_model(model, "weightedRecall", test)

print(f"TEST: Accuracy: {accuracy_test}, F1: {f1_test}, Precision: {precision_test}, Recall: {recall_test}")



TRAIN: Accuracy: 0.817933260862404, F1: 0.8166826498640659, Precision: 0.8174179578627085, Recall: 0.8179332608624041
TEST: Accuracy: 0.7986359646161119, F1: 0.7972357962860803, Precision: 0.7983870255522896, Recall: 0.7986359646161116


Le metriche sono intorno all'80%. Vediamo migliorano utilizzando la colonna summary

**Modello logistic regression per "summary"**

In [0]:
#definire il dataset con le colonne di interesse
df_sum = df_filtered_full.select("filtered_sum_tokens","categoria")

#train,test split
train,test= df_sum.randomSplit([0.8,0.2], seed=42)

# Definire le fasi della pipeline
counter_sum = CountVectorizer(inputCol="filtered_sum_tokens", outputCol="vector_sum", vocabSize=5000)
scaler_sum = StandardScaler(inputCol="vector_sum", outputCol="scaled_features_sum")
pca_sum = PCA(k=200, inputCol="scaled_features_sum", outputCol="pca_features_sum")
scaler_pca_sum = StandardScaler(inputCol="pca_features_sum", outputCol="rescaled_features_sum")
lr_sum = LogisticRegression(featuresCol="rescaled_features_sum", labelCol="categoria_indexed")

#Definire la pipeline
pipe_sum=Pipeline(stages=[indexer, counter_sum, scaler_sum, pca_sum, scaler_pca_sum, lr_sum])
# Addestrare il modello
model_sum = pipe_sum.fit(train)

Valutiamo il modello

In [0]:
#Valutare il modello per train set
accuracy_train = evaluation_model(model_sum, "accuracy", train)
f1_train = evaluation_model(model_sum, "f1", train)
precision_train = evaluation_model(model_sum, "weightedPrecision", train)
recall_train = evaluation_model(model_sum, "weightedRecall", train)

print(f"TRAIN: Accuracy: {accuracy_train}, F1: {f1_train}, Precision: {precision_train}, Recall: {recall_train}")


# Valutare il modello per test set
accuracy_test = evaluation_model(model_sum, "accuracy", test)
f1_test = evaluation_model(model_sum, "f1", test)
precision_test = evaluation_model(model_sum, "weightedPrecision", test)
recall_test = evaluation_model(model_sum, "weightedRecall", test)

# Print all evaluation results
print(f"TEST: Accuracy: {accuracy_test}, F1: {f1_test}, Precision: {precision_test}, Recall: {recall_test}")

TRAIN: Accuracy: 0.8208979806963798, F1: 0.8208331908790025, Precision: 0.8219505053741506, Recall: 0.8208979806963799
TEST: Accuracy: 0.8050509825106354, F1: 0.8046444446254486, Precision: 0.8057808800280456, Recall: 0.8050509825106353


Il modello sembra performare leggermente meglio con la colonna summary. Purtroppo non è stato possibile incrementare il vocabSize del countVectorizer in quanto oltre il valore 5000 da errore.


Vediamo se con un modello più complesso si riescono ad avere metriche migliori.

**Naive Bayes Multinomial per documents**

In [0]:

train, test = df_doc.randomSplit([0.8, 0.2], seed=42)

# Aggiunta di TF-IDF per migliorare la rappresentazione delle feature
counter = CountVectorizer(inputCol="filtered_doc_tokens", outputCol="raw_features", vocabSize=5000)
idf = IDF(inputCol="raw_features", outputCol="vector")
scaler_nb = MinMaxScaler(inputCol="vector", outputCol="scaled_features")  # Uso MinMaxScaler
nb = NaiveBayes(featuresCol="scaled_features", labelCol="categoria_indexed", smoothing=0.5, modelType="multinomial")

# Creazione della pipeline
pipe_nb = Pipeline(stages=[indexer, counter, idf, scaler_nb, nb])
# Addestrare il modello
model_nb = pipe_nb.fit(train)

Valuto il modello per train e test set


In [0]:

#valutazione train set
accuracy_train = evaluation_model(model_nb, "accuracy", train)
f1_train = evaluation_model(model_nb, "f1", train)
precision_train = evaluation_model(model_nb, "weightedPrecision", train)
recall_train = evaluation_model(model_nb, "weightedRecall", train)
print("TRAIN:")
print(accuracy_train,f1_train,precision_train,recall_train)

#valutazione test set
accuracy_test = evaluation_model(model_nb, "accuracy", test)
f1_test = evaluation_model(model_nb, "f1", test)
precision_test = evaluation_model(model_nb, "weightedPrecision", test)
recall_test = evaluation_model(model_nb, "weightedRecall", test)
print("TEST:")
print(accuracy_test,f1_test,precision_test,recall_test)

TRAIN:
0.6856738149355996 0.680441624621106 0.707638336085671 0.6856738149355999
TEST:
0.6785063137281383 0.6722836390345903 0.6982991588868532 0.6785063137281384


le metriche sono decisamente più basse. Vediamo come performa il modello con la colonna summary

**Naive bayes Multinomial con summary**

In [0]:
train, test = df_sum.randomSplit([0.8, 0.2], seed=42)

# Aggiunta di TF-IDF per migliorare la rappresentazione delle feature
counter_nb_sum = CountVectorizer(inputCol="filtered_sum_tokens", outputCol="raw_features_sum", vocabSize=5000)
idf_sum = IDF(inputCol="raw_features_sum", outputCol="vector_sum")
scaler_nb_sum = MinMaxScaler(inputCol="vector_sum", outputCol="scaled_features_sum")  # Uso MinMaxScaler
nb_sum = NaiveBayes(featuresCol="scaled_features_sum", labelCol="categoria_indexed", smoothing=0.5, modelType="multinomial")

# Creazione della pipeline
pipe_nb_sum = Pipeline(stages=[indexer, counter_nb_sum, idf_sum, scaler_nb_sum, nb_sum])
# Addestrare il modello
model_nb_sum = pipe_nb_sum.fit(train)

In [0]:
#valutazione train set
accuracy_train = evaluation_model(model_nb_sum, "accuracy", train)
f1_train = evaluation_model(model_nb_sum, "f1", train)
precision_train = evaluation_model(model_nb_sum, "weightedPrecision", train)
recall_train = evaluation_model(model_nb_sum, "weightedRecall", train)
print("TRAIN:")
print(accuracy_train,f1_train,precision_train,recall_train)

#valutazione test set
accuracy_test = evaluation_model(model_nb_sum, "accuracy", test)
f1_test = evaluation_model(model_nb_sum, "f1", test)
precision_test = evaluation_model(model_nb_sum, "weightedPrecision", test)
recall_test = evaluation_model(model_nb_sum, "weightedRecall", test)
print("TEST:")
print(accuracy_test,f1_test,precision_test,recall_test)

TRAIN:
0.7738907006621207 0.7727729172129769 0.7810362223115254 0.7738907006621207
TEST:
0.7463704504017827 0.7446163416309007 0.7523926021519866 0.7463704504017826


Le metriche del naive bayes su summary sono migliori rispetto a document ma comunque il modello migliore resta la logistic regression su colonna summary